<a href="https://colab.research.google.com/github/Jmigliatti/Calculo_metricas_infomaz/blob/main/FAISS_Enhancing_Exp.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install pycocotools

In [ ]:
!wget http://images.cocodataset.org/annotations/annotations_trainval2014.zip
!unzip annotations_trainval2014.zip
!wget http://images.cocodataset.org/zips/train2014.zip
#!wget http://images.cocodataset.org/zips/val2014.zip
!unzip train2014.zip
#!unzip val2014.zip

Streaming output truncated to the last 5000 lines.
 extracting: train2014/COCO_train2014_000000408557.jpg  
 extracting: train2014/COCO_train2014_000000013714.jpg  
 extracting: train2014/COCO_train2014_000000194043.jpg  
 extracting: train2014/COCO_train2014_000000219859.jpg  
 extracting: train2014/COCO_train2014_000000278135.jpg  
 extracting: train2014/COCO_train2014_000000141015.jpg  
 extracting: train2014/COCO_train2014_000000280923.jpg  
 extracting: train2014/COCO_train2014_000000200024.jpg  
 extracting: train2014/COCO_train2014_000000435713.jpg  
 extracting: train2014/COCO_train2014_000000249993.jpg  
 extracting: train2014/COCO_train2014_000000424160.jpg  
 extracting: train2014/COCO_train2014_000000142761.jpg  
 extracting: train2014/COCO_train2014_000000532668.jpg  
 extracting: train2014/COCO_train2014_000000564904.jpg  
 extracting: train2014/COCO_train2014_000000346384.jpg  
 extracting: train2014/COCO_train2014_000000560934.jpg  
 extracting: train2014/COCO_train2014

In [ ]:
def filename_to_id(filename: str):
    """
    Extrai o image_id de um nome de arquivo no padrão COCO.
    Exemplo: "COCO_train2014_000000123456.jpg" -> 123456
    """
    return int(filename.split('_')[-1].split('.')[0])


In [ ]:
from pycocotools.coco import COCO

dataDir = '.'
dataType = 'val2014'
annFile = f'{dataDir}/annotations/instances_{dataType}.json'

# Inicializar COCO API
coco = COCO(annFile)

loading annotations into memory...
Done (t=5.21s)
creating index...
index created!


In [ ]:
import os
import torch
from PIL import Image
from tqdm import tqdm
from transformers import CLIPProcessor, CLIPModel

# Caminhos
image_dir = "/content/train2014"
output_path = "/content/clip_embeddings_1000.pt"

# Carrega modelo CLIP ViT-L/14@336px
device = "cuda" if torch.cuda.is_available() else "cpu"
model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14-336").to(device)
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14-336")

# Função para carregar imagem
def load_image(image_path):
    return Image.open(image_path).convert("RGB")

# Extrair embeddings de até 1000 imagens
image_embeddings = {}
image_filenames = sorted([f for f in os.listdir(image_dir) if f.endswith(".jpg")])[:5000]

for filename in tqdm(image_filenames, desc="Extraindo embeddings CLIP"):
    path = os.path.join(image_dir, filename)
    image = load_image(path)
    inputs = processor(images=image, return_tensors="pt").to(device)
    with torch.no_grad():
        embedding = model.get_image_features(**inputs)
        embedding = embedding / embedding.norm(dim=-1, keepdim=True)
    image_embeddings[filename] = embedding.cpu()

# Salvar os embeddings
torch.save(image_embeddings, output_path)
print(f"Embeddings salvos: {output_path}")


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json: 0.00B [00:00, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.71G [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.71G [00:00<?, ?B/s]

Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


...

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/389 [00:00<?, ?B/s]


Extraindo embeddings CLIP: 100%|██████████| 5000/5000 [03:46<00:00, 22.09it/s]


Embeddings salvos: /content/clip_embeddings_1000.pt


In [ ]:
import torch
from transformers import CLIPProcessor, CLIPModel
from tqdm import tqdm
import torch.nn.functional as F

# Caminhos e configuração
device = "cuda" if torch.cuda.is_available() else "cpu"
clip_model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14-336").to(device)
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14-336")
image_embeddings = torch.load("/content/clip_embeddings_1000.pt")

# Convertemos para dois tensores: lista de nomes e tensor de embeddings
image_names = list(image_embeddings.keys())
image_tensor = torch.stack([image_embeddings[name].squeeze(0) for name in image_names]).to(device)

# Suponha que você tenha esse dicionário
queries = {
    "query_1": "A dog running on the grass.",
    "query_2": "A group of people riding bicycles.",
    # ...
}

top_k = 20
results = {}

for q_id, query_text in tqdm(queries.items(), desc="Realizando buscas"):
    inputs = clip_processor(text=query_text, return_tensors="pt", padding=True).to(device)
    with torch.no_grad():
        text_embedding = clip_model.get_text_features(**inputs)
        text_embedding = F.normalize(text_embedding, dim=-1)

    similarities = torch.matmul(text_embedding, image_tensor.T).squeeze(0)  # (1000,)
    top_scores, top_indices = similarities.topk(top_k)

    top_images = [image_names[i] for i in top_indices.tolist()]
    results[q_id] = {
        "query": query_text,
        "top_images": top_images,
        "scores": top_scores.cpu().tolist()
    }

# Exemplo de visualização
for q_id, data in list(results.items())[:2]:
    print(f"\nQuery: {data['query']}")
    print("Top imagens:", data["top_images"])


Realizando buscas: 100%|██████████| 2/2 [00:00<00:00,  6.11it/s]


Query: A dog running on the grass.
Top imagens: ['COCO_train2014_000000000307.jpg', 'COCO_train2014_000000010546.jpg', 'COCO_train2014_000000003623.jpg', 'COCO_train2014_000000034680.jpg', 'COCO_train2014_000000007778.jpg', 'COCO_train2014_000000030608.jpg', 'COCO_train2014_000000021048.jpg', 'COCO_train2014_000000029509.jpg', 'COCO_train2014_000000030646.jpg', 'COCO_train2014_000000032627.jpg', 'COCO_train2014_000000009640.jpg', 'COCO_train2014_000000016206.jpg', 'COCO_train2014_000000008821.jpg', 'COCO_train2014_000000012824.jpg', 'COCO_train2014_000000024036.jpg', 'COCO_train2014_000000005782.jpg', 'COCO_train2014_000000017171.jpg', 'COCO_train2014_000000005355.jpg', 'COCO_train2014_000000003862.jpg', 'COCO_train2014_000000033444.jpg']

Query: A group of people riding bicycles.
Top imagens: ['COCO_train2014_000000008025.jpg', 'COCO_train2014_000000022228.jpg', 'COCO_train2014_000000006233.jpg', 'COCO_train2014_000000014089.jpg', 'COCO_train2014_000000016346.jpg', 'COCO_train2014_00

In [ ]:
def gerar_feedback_com_base_em_categoria_alvo(qid, query_text, top_images, imagem_base_id, categoria_alvo, annotations, id_para_categoria, filename_to_id):
    """
    Gera feedback artificial com base em uma categoria-alvo.

    Retorna:
        Um dicionário contendo:
            - caption: o texto da query.
            - image_name: o ID da imagem base.
            - relevant_images: lista de IDs de imagens relevantes.
            - total_relevantes: o número total de imagens relevantes encontradas.
    """

    from collections import defaultdict

    # Criar índice invertido: image_id -> set de category_ids
    categorias_por_imagem = defaultdict(set)
    for ann in annotations:
        if 'image_id' in ann and 'category_id' in ann:
            categorias_por_imagem[ann['image_id']].add(ann['category_id'])

    # Obter o ID da categoria-alvo
    categoria_id_alvo = None
    for cid, nome in id_para_categoria.items():
        if nome == categoria_alvo:
            categoria_id_alvo = cid
            break
    if categoria_id_alvo is None:
        raise ValueError(f"Categoria '{categoria_alvo}' não encontrada no mapeamento.")

    print(f"\n========== Feedback para a query {qid} ==========")
    print(f"→ Categoria alvo: '{categoria_alvo}' (ID {categoria_id_alvo})")
    print(f"→ Total de imagens recuperadas: {len(top_images)}")

    # Identificar imagens relevantes
    relevantes_ids = []
    for filename in top_images:
        img_id = filename_to_id(filename)
        categorias_da_imagem = categorias_por_imagem.get(img_id, set())
        if categoria_id_alvo in categorias_da_imagem:
            relevantes_ids.append(img_id)
            nomes_categorias = [id_para_categoria[cid] for cid in categorias_da_imagem]
            print(f"✓ Imagem {filename} (ID {img_id}) é relevante")
            print(f"    → Categorias da imagem: {nomes_categorias}")
        else:
            nomes_categorias = [id_para_categoria[cid] for cid in categorias_da_imagem]
            print(f"✗ Imagem {filename} (ID {img_id}) não é relevante")
            print(f"    → Categorias da imagem: {nomes_categorias}")

    total_relevantes = len(relevantes_ids)
    print(f"\n→ Total de imagens relevantes encontradas: {total_relevantes}")
    if len(top_images) > 0:
        porcentagem = (total_relevantes / len(top_images)) * 100
        print(f"→ Porcentagem de relevantes no top {len(top_images)}: {porcentagem:.2f}%")

    # Retornar os resultados com a quantidade de relevantes encontradas
    return {
    "caption": query_text,
    "image_name": imagem_base_id,
    "relevant_images": relevantes_ids,
    "total_relevantes": total_relevantes
}

In [ ]:
from collections import defaultdict

def calcular_recall_at_k(
    num_relevantes_encontrados,
    categoria_alvo,
    categoria_por_id,
    annotations,
    image_embeddings,
    ks=[20, 40, 60],
    max_relevantes=20,
    filename_to_id=None,
    debug=False
):
    """
    Calcula Recall@k considerando todas as imagens da categoria alvo no conjunto de busca.

    Em vez de receber todos os resultados recuperados, agora recebe apenas o número de
    relevantes encontradas nos top-k resultados.

    Parâmetros:
        num_relevantes_encontrados: dict {qid: {k: número de relevantes encontrados em top-k}}
        categoria_alvo: str (categoria relevante, ex: "gato")
        categoria_por_id: dict {id_numérico: categoria}
        annotations: lista de anotações contendo image_id e category_id
        image_embeddings: dict {nome_imagem: embedding} (para extrair lista de imagens)
        ks: lista de valores de k (default [20, 40, 60])
        max_relevantes: número máximo de relevantes considerados (default 20)
        filename_to_id: dict {nome_imagem: image_id}
        debug: bool (ativa prints de depuração)

    Retorna:
        dict {k: recall médio em todas as queries}
    """
    if filename_to_id is None:
        raise ValueError("filename_to_id precisa ser fornecido.")

    # Passo 1: Criar índice invertido: image_id -> set de category_ids
    categorias_por_imagem = defaultdict(set)
    for ann in annotations:
        categorias_por_imagem[ann['image_id']].add(ann['category_id'])

    # Passo 2: Mapear nomes para image_ids
    filename_to_img_id = {}
    for filename in image_embeddings.keys():
        if filename not in filename_to_id:
            continue
        filename_to_img_id[filename] = filename_to_id[filename]

    # Passo 3: Identificar imagens relevantes
    relevantes_globais_filenames = set()
    for filename, img_id in filename_to_img_id.items():
        categorias = categorias_por_imagem.get(img_id, set())
        for cat_id in categorias:
            if categoria_por_id.get(cat_id) == categoria_alvo:
                relevantes_globais_filenames.add(filename)
                break

    # Ordenar antes de truncar para manter determinismo
    relevantes_globais_filenames = sorted(relevantes_globais_filenames)
    relevantes_globais_filenames = set(relevantes_globais_filenames[:max_relevantes])

    if debug:
        print(f"\n[INFO] Total de imagens relevantes no conjunto de busca: {len(relevantes_globais_filenames)}")
        print(f"[INFO] Imagens relevantes (até 10): {list(relevantes_globais_filenames)[:10]}\n")

    if not relevantes_globais_filenames:
        return {k: 0.0 for k in ks}

    # Passo 4: Calcular Recall@k
    recalls_acumulados = {k: 0.0 for k in ks}
    total_queries = 0

    for qid, relevantes_k in num_relevantes_encontrados.items():
        total_queries += 1

        if debug:
            print(f"Query {qid}: número de relevantes encontradas nos top-k: {relevantes_k}")

        for k in ks:
            # O número de relevantes encontradas no top-k é fornecido diretamente
            recalls_acumulados[k] += relevantes_k[k] / len(relevantes_globais_filenames)

            if debug:
                print(f"Recall@{k} para query {qid}: {relevantes_k[k]} acertos em {len(relevantes_globais_filenames)} relevantes")

    return {k: recalls_acumulados[k] / total_queries if total_queries else 0.0 for k in ks}


In [ ]:
import json
from collections import defaultdict

# Caminho para o arquivo de anotações
annotations_path = "/content/annotations/captions_train2014.json"

# Carrega o arquivo JSON
with open(annotations_path, 'r') as f:
    coco_data = json.load(f)

# Cria um dicionário image_id -> [legendas]
captions_dict = defaultdict(list)
for ann in coco_data['annotations']:
    image_id = ann['image_id']
    caption = ann['caption']
    captions_dict[image_id].append(caption)

# Mapeia image_id para nome de arquivo (conforme padrão COCO)
def image_id_to_filename(image_id):
    return f"COCO_train2014_{int(image_id):012d}.jpg"

# Pega os 10 primeiros image_ids únicos
first_10_ids = list(captions_dict.keys())[:10]

# Imprime as legendas
for i, image_id in enumerate(first_10_ids):
    filename = image_id_to_filename(image_id)
    print(f"\n[{i+1}] {filename}")
    for caption in captions_dict[image_id]:
        print(f"  - {caption}")



[1] COCO_train2014_000000318556.jpg
  - A very clean and well decorated empty bathroom
  - A blue and white bathroom with butterfly themed wall tiles.
  - A bathroom with a border of butterflies and blue paint on the walls above it.
  - An angled view of a beautifully decorated bathroom.
  - A clock that blends in with the wall hangs in a bathroom. 

[2] COCO_train2014_000000116100.jpg
  - A panoramic view of a kitchen and all of its appliances.
  - A panoramic photo of a kitchen and dining room
  - A wide angle view of the kitchen work area
  - multiple photos of a brown and white kitchen. 
  - A kitchen that has a checkered patterned floor and white cabinets.

[3] COCO_train2014_000000379340.jpg
  - A graffiti-ed stop sign across the street from a red car 
  - A vandalized stop sign and a red beetle on the road
  - A red stop sign with a Bush bumper sticker under the word stop.
  - A stop sign that has been vandalized is pictured in front of a parked car.
  - A street sign modified 

In [ ]:
import json

# Caminho para as anotações
annotations_path = "/content/annotations/captions_train2014.json"

# Carrega as anotações
with open(annotations_path, 'r') as f:
    coco_data = json.load(f)

# IDs de imagens para as quais extraímos embeddings
imagem_names = set(image_embeddings.keys())

# Função para converter image_id para o nome padrão de arquivo COCO
def image_id_to_filename(image_id):
    return f"COCO_train2014_{image_id:012d}.jpg"

# Montar apenas queries válidas
queries = {}
query_id = 0
for ann in coco_data['annotations']:
    img_id = ann['image_id']
    filename = image_id_to_filename(img_id)
    if filename in imagem_names:
        queries[f"q{query_id}"] = {
            "caption": ann['caption'],
            "image_name": filename
        }
        query_id += 1

# Mostrar informações
print(f"Total de queries válidas: {len(queries)}\n")

# Mostrar um exemplo
exemplo_qid = next(iter(queries))
exemplo = queries[exemplo_qid]

print(f"Exemplo de query (ID: {exemplo_qid}):")
print(json.dumps(exemplo, indent=2))

# Verificação cruzada
img_file = exemplo['image_name']
print(f"\nVerificação: '{img_file}' está em image_embeddings? {'Sim' if img_file in imagem_names else 'Não'}")


Total de queries válidas: 25015

Exemplo de query (ID: q0):
{
  "caption": "The vanity contains two sinks with a towel for each.",
  "image_name": "COCO_train2014_000000032275.jpg"
}

Verificação: 'COCO_train2014_000000032275.jpg' está em image_embeddings? Sim


In [ ]:
# Cria um dicionário image_id -> filename
def image_id_to_filename(image_id):
    return f"COCO_train2014_{image_id:012d}.jpg"

filename_to_id = {}
for img in coco_data['images']:
    image_id = img['id']
    filename = image_id_to_filename(image_id)
    filename_to_id[filename] = image_id


In [ ]:
import json

# Caminho para o arquivo de anotações
caminho_anotacoes = "/content/annotations/instances_train2014.json"

# Carregar o JSON
with open(caminho_anotacoes, "r") as f:
    coco_data = json.load(f)

# Exibir as chaves principais
print("Chaves principais:", coco_data.keys())

# Exibir um exemplo de imagem
print("\nExemplo de imagem:")
print(coco_data["images"][0])

# Exibir um exemplo de anotação (ligação entre imagem e categoria)
print("\nExemplo de anotação:")
print(coco_data["annotations"][0])

# Exibir as categorias
print("\nCategorias:")
print(coco_data["categories"])


Chaves principais: dict_keys(['info', 'images', 'licenses', 'annotations', 'categories'])

Exemplo de imagem:
{'license': 5, 'file_name': 'COCO_train2014_000000057870.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000057870.jpg', 'height': 480, 'width': 640, 'date_captured': '2013-11-14 16:28:13', 'flickr_url': 'http://farm4.staticflickr.com/3153/2970773875_164f0c0b83_z.jpg', 'id': 57870}

Exemplo de anotação:
{'segmentation': [[312.29, 562.89, 402.25, 511.49, 400.96, 425.38, 398.39, 372.69, 388.11, 332.85, 318.71, 325.14, 295.58, 305.86, 269.88, 314.86, 258.31, 337.99, 217.19, 321.29, 182.49, 343.13, 141.37, 348.27, 132.37, 358.55, 159.36, 377.83, 116.95, 421.53, 167.07, 499.92, 232.61, 560.32, 300.72, 571.89]], 'area': 54652.9556, 'iscrowd': 0, 'image_id': 480023, 'bbox': [116.95, 305.86, 285.3, 266.03], 'category_id': 58, 'id': 86}

Categorias:
[{'supercategory': 'person', 'id': 1, 'name': 'person'}, {'supercategory': 'vehicle', 'id': 2, 'name': 'bicycl

In [ ]:
# Criar dicionário de mapeamento de id para nome
id_para_categoria = {cat['id']: cat['name'] for cat in coco_data["categories"]}


In [ ]:
import json

# Caminho para o arquivo de anotações
caminho_anotacoes = "/content/annotations/instances_train2014.json"

# Carregar o JSON
with open(caminho_anotacoes, "r") as f:
    coco_data = json.load(f)

# Exibir as chaves principais
print("Chaves principais:", coco_data.keys())

# Exibir um exemplo de imagem
print("\nExemplo de imagem:")
print(coco_data["images"][0])

# Exibir um exemplo de anotação (ligação entre imagem e categoria)
print("\nExemplo de anotação:")
print(coco_data["annotations"][0])

# Exibir as categorias
print("\nCategorias:")
print(coco_data["categories"])


Chaves principais: dict_keys(['info', 'images', 'licenses', 'annotations', 'categories'])

Exemplo de imagem:
{'license': 5, 'file_name': 'COCO_train2014_000000057870.jpg', 'coco_url': 'http://images.cocodataset.org/train2014/COCO_train2014_000000057870.jpg', 'height': 480, 'width': 640, 'date_captured': '2013-11-14 16:28:13', 'flickr_url': 'http://farm4.staticflickr.com/3153/2970773875_164f0c0b83_z.jpg', 'id': 57870}

Exemplo de anotação:
{'segmentation': [[312.29, 562.89, 402.25, 511.49, 400.96, 425.38, 398.39, 372.69, 388.11, 332.85, 318.71, 325.14, 295.58, 305.86, 269.88, 314.86, 258.31, 337.99, 217.19, 321.29, 182.49, 343.13, 141.37, 348.27, 132.37, 358.55, 159.36, 377.83, 116.95, 421.53, 167.07, 499.92, 232.61, 560.32, 300.72, 571.89]], 'area': 54652.9556, 'iscrowd': 0, 'image_id': 480023, 'bbox': [116.95, 305.86, 285.3, 266.03], 'category_id': 58, 'id': 86}

Categorias:
[{'supercategory': 'person', 'id': 1, 'name': 'person'}, {'supercategory': 'vehicle', 'id': 2, 'name': 'bicycl

In [ ]:
def recuperar_imagens_clip(consultas, image_embeddings, clip_model, clip_processor, top_k=20):
    image_names = list(image_embeddings.keys())
    image_tensor = torch.stack([image_embeddings[n].squeeze(0) for n in image_names])
    image_tensor = image_tensor.to(clip_model.device)

    resultados = {}

    for qid, query_text in consultas.items():
        inputs = clip_processor(
            text=query_text,
            return_tensors="pt",
            padding=True,
            truncation=True
        ).to(clip_model.device)

        with torch.no_grad():
            text_embedding = clip_model.get_text_features(**inputs)
            text_embedding = F.normalize(text_embedding, dim=-1)

        similarities = torch.matmul(text_embedding, image_tensor.T).squeeze(0)
        top_scores, top_indices = similarities.topk(top_k)

        top_images = [image_names[i] for i in top_indices.tolist()]
        resultados[qid] = {
            "query": query_text,
            "top_images": top_images,
            "scores": top_scores.cpu().tolist()
        }
        print(f"Query: {query_text}")
        print("Top imagens:", top_images)

    return resultados


In [ ]:
def filename_to_id(filename: str):
    """
    Extrai o image_id de um nome de arquivo no padrão COCO.
    Exemplo: "COCO_train2014_000000123456.jpg" -> 123456
    """
    return int(filename.split('_')[-1].split('.')[0])


In [ ]:
from collections import defaultdict
import random

def escolher_categoria_alvo_da_imagem_base(imagem_base_id, annotations, id_para_categoria):
    """
    Escolhe aleatoriamente uma categoria presente na imagem base.

    Args:
        imagem_base_id (int): ID da imagem base.
        annotations (list[dict]): Lista de anotações do COCO.
        id_para_categoria (dict): Mapeia category_id para o nome da categoria.

    Retorna:
        str: Nome da categoria alvo escolhida.
    """
    # Coletar as categorias da imagem base
    categorias_base = {ann['category_id'] for ann in annotations if ann['image_id'] == imagem_base_id}

    if not categorias_base:
        raise ValueError(f"Nenhuma categoria encontrada para a imagem {imagem_base_id}.")

    categoria_escolhida_id = random.choice(list(categorias_base))
    return id_para_categoria[categoria_escolhida_id]


In [ ]:
import json

with open('/content/annotations/instances_train2014.json') as f:
    coco_data = json.load(f)

annotations = coco_data['annotations']


In [ ]:
# Número máximo de queries
num_queries = 100

# Seleciona apenas as primeiras N queries
queries_reduzidas = dict(list(queries.items())[:num_queries])

In [ ]:
import torch
from PIL import Image
from transformers import InstructBlipProcessor, InstructBlipForConditionalGeneration

# Modelo utilizado no artigo
model_id = "Salesforce/instructblip-vicuna-7b"

# Usa float16 para economizar VRAM
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
dtype = torch.float16 if device.type == "cuda" else torch.float32

# Carregando modelo e processor
print("Carregando modelo InstructBLIP (Vicuna-7B)...")
processor = InstructBlipProcessor.from_pretrained(model_id)
model = InstructBlipForConditionalGeneration.from_pretrained(
    model_id,
    torch_dtype=dtype
).to(device)

# Geração de legenda conforme configuração do artigo
def gerar_legenda_instructblip(image_path, prompt="A short image caption:"):
    image = Image.open(image_path).convert("RGB")
    inputs = processor(images=image, text=prompt, return_tensors="pt").to(device)
    with torch.no_grad():
        outputs = model.generate(**inputs, max_new_tokens=100)
    caption = processor.batch_decode(outputs, skip_special_tokens=True)[0].strip()
    return caption


Carregando modelo InstructBLIP (Vicuna-7B)...


preprocessor_config.json:   0%|          | 0.00/439 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

...

model-00002-of-00004.safetensors:   0%|          | 0.00/9.96G [00:00<?, ?B/s]

model-00004-of-00004.safetensors:   0%|          | 0.00/1.88G [00:00<?, ?B/s]

model-00001-of-00004.safetensors:   0%|          | 0.00/9.90G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/141 [00:00<?, ?B/s]

In [ ]:
from transformers import pipeline
import torch

# Carregar o modelo
denoise_model_id = "google/flan-t5-xl"
device_id = 0 if torch.cuda.is_available() else -1
llm = pipeline("text2text-generation", model=denoise_model_id, tokenizer=denoise_model_id, device=device_id)

def denoise_chain_of_thought(query_expandida):
    prompt = (
        "Given the image descriptions, generate a list of keywords and a new description based on generated keywords\n\n"
        "Image captions:\n"
        f"{query_expandida}\n\n"
    )

    response = llm(prompt, max_new_tokens=50)[0]["generated_text"].strip()

    return response


config.json: 0.00B [00:00, ?B/s]

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/1.95G [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.45G [00:00<?, ?B/s]

...

tokenizer_config.json: 0.00B [00:00, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

Device set to use cuda:0


In [ ]:
def expandir_consulta(feedback_dict, image_dir="/content/train2014"):
    consultas_denoised = {}
    for qid, data in feedback_dict.items():
        original = data["caption"]
        imagens = data["relevant_images"]

        legendas = []
        for image_id in imagens:
          filename = image_id_to_filename(image_id)
          path = os.path.join(image_dir, filename)
          try:
            legenda = gerar_legenda_instructblip(path)
            legendas.append(legenda)
          except Exception as e:
            print(f"Erro na imagem {img_name}: {e}")

        query_expandida = original + " " + " ".join(legendas)
        query_denoised = denoise_chain_of_thought(query_expandida)

        consultas_denoised[qid] = query_denoised

        print(f"\n{qid} (Imagem base: {data['image_name']}):")
        print(f"Original: {original}")
        print(f"Expandida: {query_expandida}")
        print(f"Denoised: {query_denoised}")

    return consultas_denoised


In [ ]:
def image_id_to_filename(image_id):
    if isinstance(image_id, int):
        return f"COCO_train2014_{image_id:012d}.jpg"
    elif isinstance(image_id, str) and image_id.endswith('.jpg'):
        return image_id
    else:
        return f"COCO_train2014_{int(image_id):012d}.jpg"



In [ ]:
from collections import defaultdict

def calcular_recall_at_k(
    num_relevantes_encontrados,
    categoria_alvo,
    categoria_por_id,
    annotations,
    image_embeddings,
    ks=[20, 40, 60],
    max_relevantes=20,
    filename_to_id=None,
    debug=False
):
    """
    Calcula Recall@k considerando todas as imagens da categoria alvo no conjunto de busca.

    Em vez de receber todos os resultados recuperados, agora recebe apenas o número de
    relevantes encontradas nos top-k resultados.

    Parâmetros:
        num_relevantes_encontrados: dict {qid: {k: número de relevantes encontrados em top-k}}
        categoria_alvo: str (categoria relevante, ex: "gato")
        categoria_por_id: dict {id_numérico: categoria}
        annotations: lista de anotações contendo image_id e category_id
        image_embeddings: dict {nome_imagem: embedding} (para extrair lista de imagens)
        ks: lista de valores de k (default [20, 40, 60])
        max_relevantes: número máximo de relevantes considerados (default 20)
        filename_to_id: dict {nome_imagem: image_id}
        debug: bool (ativa prints de depuração)

    Retorna:
        dict {k: recall médio em todas as queries}
    """
    if filename_to_id is None:
        raise ValueError("filename_to_id precisa ser fornecido.")

    # Passo 1: Criar índice invertido: image_id -> set de category_ids
    categorias_por_imagem = defaultdict(set)
    for ann in annotations:
        categorias_por_imagem[ann['image_id']].add(ann['category_id'])

    # Passo 2: Mapear nomes para image_ids
    filename_to_img_id = {}
    for filename in image_embeddings.keys():
        if filename not in filename_to_id:
            continue
        filename_to_img_id[filename] = filename_to_id[filename]

    # Passo 3: Identificar imagens relevantes
    relevantes_globais_filenames = set()
    for filename, img_id in filename_to_img_id.items():
        categorias = categorias_por_imagem.get(img_id, set())
        for cat_id in categorias:
            if categoria_por_id.get(cat_id) == categoria_alvo:
                relevantes_globais_filenames.add(filename)
                break

    # Ordenar antes de truncar para manter determinismo
    relevantes_globais_filenames = sorted(relevantes_globais_filenames)
    relevantes_globais_filenames = set(relevantes_globais_filenames[:max_relevantes])

    if debug:
        print(f"\n[INFO] Total de imagens relevantes no conjunto de busca: {len(relevantes_globais_filenames)}")
        print(f"[INFO] Imagens relevantes (até 10): {list(relevantes_globais_filenames)[:10]}\n")

    # Passo 4: Calcular Recall@k

    print(f"Recall@20 para query {qid}: {num_relevantes_encontrados} acertos em {len(relevantes_globais_filenames)} relevantes")

    return {num_relevantes_encontrados / len(relevantes_globais_filenames)}


In [ ]:
def calcular_recall_at_20(num_relevantes_encontrados, max_relevantes=20):
    if max_relevantes == 0:
        return 0.0
    return min(num_relevantes_encontrados / max_relevantes, 1.0)


In [ ]:
pip install faiss-cpu  # ou faiss-gpu se você tiver GPU


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.3/31.3 MB 78.6 MB/s eta 0:00:00


In [ ]:
import faiss
import torch
import torch.nn.functional as F
import numpy as np

def recuperar_imagens_clip(
    consultas,
    image_embeddings,
    clip_model,
    clip_processor,
    top_k=20,
    metodo="cosine"  # opções: 'cosine', 'euclidean', 'faiss'
):
    image_names = list(image_embeddings.keys())
    image_tensor = torch.stack([image_embeddings[n].squeeze(0) for n in image_names])
    image_tensor = image_tensor.to(clip_model.device)

    resultados = {}

    if metodo in ['cosine', 'faiss']:
        image_tensor = F.normalize(image_tensor, dim=-1)

    if metodo == 'faiss':
        # Prepara índice FAISS com inner product (equivalente à cosine se vetores forem normalizados)
        d = image_tensor.shape[1]
        index = faiss.IndexFlatIP(d)
        index.add(image_tensor.cpu().numpy())  # FAISS requer numpy no CPU

    for qid, query_text in consultas.items():
        inputs = clip_processor(
            text=query_text,
            return_tensors="pt",
            padding=True,
            truncation=True
        ).to(clip_model.device)

        with torch.no_grad():
            text_embedding = clip_model.get_text_features(**inputs)

            if metodo in ['cosine', 'faiss']:
                text_embedding = F.normalize(text_embedding, dim=-1)

        if metodo == "cosine":
            similarities = torch.matmul(text_embedding, image_tensor.T).squeeze(0)
            top_scores, top_indices = similarities.topk(top_k)
        elif metodo == "euclidean":
            dists = torch.cdist(text_embedding, image_tensor, p=2).squeeze(0)
            top_scores, top_indices = (-dists).topk(top_k)
        elif metodo == "faiss":
            query_np = text_embedding.cpu().numpy()
            top_scores_np, top_indices_np = index.search(query_np, top_k)
            top_scores = torch.tensor(top_scores_np[0])
            top_indices = torch.tensor(top_indices_np[0])
        else:
            raise ValueError(f"Método de recuperação desconhecido: {metodo}")

        top_images = [image_names[i] for i in top_indices.tolist()]
        resultados[qid] = {
            "query": query_text,
            "top_images": top_images,
            "scores": top_scores.cpu().tolist()
        }

        print(f"\nQuery: {query_text}")
        print(f"Método: {metodo}")
        print("Top imagens:", top_images)

    return resultados


In [ ]:
def gerar_feedback_com_base_em_categoria_alvo(qid, query_text, top_images, imagem_base_id, categoria_alvo, annotations, id_para_categoria, filename_to_id):
    from collections import defaultdict

    categorias_por_imagem = defaultdict(set)
    for ann in annotations:
        if 'image_id' in ann and 'category_id' in ann:
            categorias_por_imagem[ann['image_id']].add(ann['category_id'])

    categoria_id_alvo = None
    for cid, nome in id_para_categoria.items():
        if nome == categoria_alvo:
            categoria_id_alvo = cid
            break
    if categoria_id_alvo is None:
        raise ValueError(f"Categoria '{categoria_alvo}' não encontrada no mapeamento.")

    print(f"\n========== Feedback para a query {qid} ==========")
    print(f"→ Categoria alvo: '{categoria_alvo}' (ID {categoria_id_alvo})")
    print(f"→ Total de imagens recuperadas: {len(top_images)}")

    relevantes_ids = []
    for filename in top_images:
        img_id = filename_to_id[filename]
        categorias_da_imagem = categorias_por_imagem.get(img_id, set())
        if categoria_id_alvo in categorias_da_imagem:
            relevantes_ids.append(img_id)
            nomes_categorias = [id_para_categoria[cid] for cid in categorias_da_imagem]
            print(f"✓ Imagem {filename} (ID {img_id}) é relevante")
            print(f"    → Categorias da imagem: {nomes_categorias}")
        else:
            nomes_categorias = [id_para_categoria[cid] for cid in categorias_da_imagem]
            print(f"✗ Imagem {filename} (ID {img_id}) não é relevante")
            print(f"    → Categorias da imagem: {nomes_categorias}")

    total_relevantes = len(relevantes_ids)
    print(f"\n→ Total de imagens relevantes encontradas: {total_relevantes}")
    if len(top_images) > 0:
        porcentagem = (total_relevantes / len(top_images)) * 100
        print(f"→ Porcentagem de relevantes no top {len(top_images)}: {porcentagem:.2f}%")

    # Construindo o feedback corretamente
    feedback = {
        'caption': query_text,
        'image_name': imagem_base_id,
        'relevant_images': [filename_to_id[f] for f in top_images if filename_to_id[f] in relevantes_ids],
        'total_relevantes': total_relevantes
    }

    return feedback


In [ ]:
def pipeline_interativo_base(queries_reduzidas, annotations, id_para_categoria, image_embeddings,
                             clip_model, clip_processor, filename_to_id_dict, image_dir="/content/train2014",
                             num_iteracoes=10, metodo_recuperacao="dot"):

    resultados_totais = {}
    recalls_por_iteracao = {i: [] for i in range(1, num_iteracoes + 1)}

    for qid, query_data in list(queries_reduzidas.items()):
        print(f"\n########## Processando query {qid} ##########")

        query_text = query_data['caption']
        imagem_base_id = filename_to_id_dict[query_data['image_name']]
        categoria_alvo = escolher_categoria_alvo_da_imagem_base(imagem_base_id, annotations, id_para_categoria)
        print(f"Categoria alvo inicial: {categoria_alvo}")

        query_resultados = {}

        for iteracao in range(1, num_iteracoes + 1):
            print(f"\n=== Iteração {iteracao} para query {qid} ===")

            # Recuperação com método especificado
            consultas = {qid: query_text}
            top_images_result = recuperar_imagens_clip(
                consultas, image_embeddings, clip_model, clip_processor,
                top_k=40, metodo=metodo_recuperacao
            )
            top_images = top_images_result[qid]['top_images']
            print(f"Top imagens recuperadas na iteração {iteracao}: {top_images}")

            # Gerar feedback (retorna dicionário com qid como chave)
            feedback_info = gerar_feedback_com_base_em_categoria_alvo(
                qid=qid,
                query_text=query_text,
                top_images=top_images,
                imagem_base_id=imagem_base_id,
                categoria_alvo=categoria_alvo,
                annotations=annotations,
                id_para_categoria=id_para_categoria,
                filename_to_id=filename_to_id_dict
            )
            feedback_dict = {qid: feedback_info}


            print(f"Feedback gerado: {feedback_dict}")

            # Pega os dados da query
            feedback_info = feedback_dict[qid]
            total_relevantes = feedback_info['total_relevantes']

            # Cálculo do recall@40
            recall = calcular_recall_at_20(num_relevantes_encontrados=total_relevantes, max_relevantes=40)
            print(f"Recall@40 na iteração {iteracao}: {recall:.4f}")
            recalls_por_iteracao[iteracao].append(recall)

            # Armazenamento dos resultados da iteração
            query_resultados[f'iteracao_{iteracao}'] = {
                'recall@40': recall,
                'top_images': top_images,
                'feedback': feedback_info
            }

            # Expansão da consulta (usando o formato esperado pela função)
            if iteracao < num_iteracoes:
                expanded_query_dict = expandir_consulta(feedback_dict, image_dir)
                query_text = expanded_query_dict[qid]
                print(f"Consulta expandida: {query_text}")

        # Armazenar resultados da query completa
        resultados_totais[qid] = query_resultados

    # Média por iteração
    print(f"\n##### MÉDIA DE RECALLS POR ITERAÇÃO ({metodo_recuperacao.upper()}) #####")
    for iteracao, recalls in recalls_por_iteracao.items():
        media = sum(recalls) / len(recalls) if recalls else 0.0
        print(f"Iteração {iteracao}: Recall@40: {media:.4f}")

    resultados_totais['media_recalls_por_iteracao'] = {
        i: sum(valores) / len(valores) if valores else 0.0
        for i, valores in recalls_por_iteracao.items()
    }

    return resultados_totais


In [ ]:
def pipeline_interativo_faiss(*args, **kwargs):
    return pipeline_interativo_base(*args, metodo_recuperacao='faiss', **kwargs)

In [ ]:
def pipeline_interativo_cosine(*args, **kwargs):
    return pipeline_interativo_base(*args, metodo_recuperacao='cosine', **kwargs)


In [ ]:
def pipeline_interativo_euclidean(*args, **kwargs):
    return pipeline_interativo_base(*args, metodo_recuperacao='euclidean', **kwargs)

In [ ]:
filenames = list(image_embeddings.keys())

filename_to_id_dict = {filename: filename_to_id(filename) for filename in filenames}

In [ ]:
resultados_cosine = pipeline_interativo_cosine(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)



########## Processando query q0 ##########
Categoria alvo inicial: sink

=== Iteração 1 para query q0 ===

Query: The vanity contains two sinks with a towel for each.
Método: cosine
Top imagens: ['COCO_train2014_000000004830.jpg', 'COCO_train2014_000000002197.jpg', 'COCO_train2014_000000032275.jpg', 'COCO_train2014_000000012103.jpg', 'COCO_train2014_000000017644.jpg', 'COCO_train2014_000000020652.jpg', 'COCO_train2014_000000016543.jpg', 'COCO_train2014_000000002024.jpg', 'COCO_train2014_000000018820.jpg', 'COCO_train2014_000000020903.jpg', 'COCO_train2014_000000019818.jpg', 'COCO_train2014_000000006842.jpg', 'COCO_train2014_000000033074.jpg', 'COCO_train2014_000000024136.jpg', 'COCO_train2014_000000032655.jpg', 'COCO_train2014_000000009195.jpg', 'COCO_train2014_000000030391.jpg', 'COCO_train2014_000000011146.jpg', 'COCO_train2014_000000022026.jpg', 'COCO_train2014_000000014774.jpg', 'COCO_train2014_000000017481.jpg', 'COCO_train2014_000000019023.jpg', 'COCO_train2014_000000007584.jpg'

Token indices sequence length is longer than the specified maximum sequence length for this model (730 > 512). Running this sequence through the model will result in indexing errors


Streaming output truncated to the last 5000 lines.
Feedback gerado: {'q95': {'caption': 'A woman riding a bike with a basket while talking on a cell phone.', 'image_name': 3988, 'relevant_images': [3988, 16616, 8055, 27227, 17520, 26132, 5638, 8657, 34611, 27142, 28555, 16737, 8309], 'total_relevantes': 13}}
Recall@40 na iteração 1: 0.3250

q95 (Imagem base: 3988):
Original: A woman riding a bike with a basket while talking on a cell phone.
Expandida: A woman riding a bike with a basket while talking on a cell phone. A short image caption: a woman riding a bike with a basket on it A short image caption: a woman riding a bike on a city street A short image caption: a man sitting on a bike in front of a store A short image caption: a woman sitting on a bench in a park A short image caption: a couple of people walking down a path near a lake A short image caption: a woman standing on a lawn mower talking on a cell phone A short image caption: a couple of people riding a motorcycle down a 

In [ ]:
resultados_faiss = pipeline_interativo_faiss(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)

Streaming output truncated to the last 5000 lines.
Feedback gerado: {'q95': {'caption': 'A woman riding a bike with a basket while talking on a cell phone.', 'image_name': 3988, 'relevant_images': [3988, 16616, 34551, 8055, 18171, 4331, 86, 30395, 27227, 17520, 16470, 9999, 21528, 26132, 8025, 34815, 2135, 22228, 30643, 5638, 20962, 8657, 34611, 14698, 30665, 1315, 27142, 28555, 4981, 16737, 17573, 24714, 6233, 8309, 14089, 29523, 28097], 'total_relevantes': 37}}
Recall@40 na iteração 1: 0.9250

q95 (Imagem base: 3988):
Original: A woman riding a bike with a basket while talking on a cell phone.
Expandida: A woman riding a bike with a basket while talking on a cell phone. A short image caption: a woman riding a bike with a basket on it A short image caption: a woman riding a bike on a city street A short image caption: a woman riding a bike with an umbrella A short image caption: a man sitting on a bike in front of a store A short image caption: a person riding a bike on a bridge over 

In [ ]:
resultados_euclidean = pipeline_interativo_euclidean(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)


########## Processando query q0 ##########
Categoria alvo inicial: sink

=== Iteração 1 para query q0 ===

Query: The vanity contains two sinks with a towel for each.
Método: euclidean
Top imagens: ['COCO_train2014_000000004830.jpg', 'COCO_train2014_000000002197.jpg', 'COCO_train2014_000000032275.jpg', 'COCO_train2014_000000012103.jpg', 'COCO_train2014_000000017644.jpg', 'COCO_train2014_000000020652.jpg', 'COCO_train2014_000000016543.jpg', 'COCO_train2014_000000002024.jpg', 'COCO_train2014_000000018820.jpg', 'COCO_train2014_000000020903.jpg', 'COCO_train2014_000000019818.jpg', 'COCO_train2014_000000006842.jpg', 'COCO_train2014_000000033074.jpg', 'COCO_train2014_000000024136.jpg', 'COCO_train2014_000000032655.jpg', 'COCO_train2014_000000009195.jpg', 'COCO_train2014_000000030391.jpg', 'COCO_train2014_000000011146.jpg', 'COCO_train2014_000000022026.jpg', 'COCO_train2014_000000014774.jpg', 'COCO_train2014_000000017481.jpg', 'COCO_train2014_000000019023.jpg', 'COCO_train2014_000000007584.j

Token indices sequence length is longer than the specified maximum sequence length for this model (730 > 512). Running this sequence through the model will result in indexing errors



q0 (Imagem base: 32275):
Original: The vanity contains two sinks with a towel for each.
Expandida: The vanity contains two sinks with a towel for each. A short image caption: a bathroom with a double sink and a mirror A short image caption: a bathroom with two sinks and a shower A short image caption: a bathroom with a double sink and a shower A short image caption: a bathroom with a sink, mirror, and towels A short image caption: a man taking a picture of a bathroom with a marble counter A short image caption: a bathroom with a toilet, sink, and towels A short image caption: a bathroom with a sink, mirror, toilet and a light A short image caption: a bathroom sink with a mirror and a toilet paper roll A short image caption: a bathroom with a sink, mirror, and towels A short image caption: a bathroom sink with a towel and a vase of flowers A short image caption: a bathroom with a sink, mirror and shelf A short image caption: two cats in the sinks of a bathroom A short image caption: a 

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


Streaming output truncated to the last 5000 lines.
Feedback gerado: {'q95': {'caption': 'A woman riding a bike with a basket while talking on a cell phone.', 'image_name': 3988, 'relevant_images': [3988, 34551, 86, 27227, 17520, 9999, 34815, 2135, 22228, 8657, 30665, 4981, 24714, 29523], 'total_relevantes': 14}}
Recall@40 na iteração 1: 0.3500

q95 (Imagem base: 3988):
Original: A woman riding a bike with a basket while talking on a cell phone.
Expandida: A woman riding a bike with a basket while talking on a cell phone. A short image caption: a woman riding a bike with a basket on it A short image caption: a woman riding a bike with an umbrella A short image caption: a man riding a motorcycle on a dirt road A short image caption: a woman sitting on a bench in a park A short image caption: a couple of people walking down a path near a lake A short image caption: a man standing on a street corner in a city A short image caption: a man and a woman with bikes standing next to a train A sh

In [ ]:
# keywords
def denoise_chain_of_thought(query_expandida):
    prompt = (
        "Given the image descriptions, generate a list of video taggings\n\n"
        "Image captions:\n"
        f"{query_expandida}\n\n"
    )

    response = llm(prompt, max_new_tokens=50)[0]["generated_text"].strip()

    return response

In [ ]:
resultados_faiss_keywords = pipeline_interativo_faiss(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)


########## Processando query q0 ##########
Categoria alvo inicial: sink

=== Iteração 1 para query q0 ===

Query: The vanity contains two sinks with a towel for each.
Método: faiss
Top imagens: ['COCO_train2014_000000004830.jpg', 'COCO_train2014_000000002197.jpg', 'COCO_train2014_000000032275.jpg', 'COCO_train2014_000000012103.jpg', 'COCO_train2014_000000017644.jpg', 'COCO_train2014_000000020652.jpg', 'COCO_train2014_000000016543.jpg', 'COCO_train2014_000000002024.jpg', 'COCO_train2014_000000018820.jpg', 'COCO_train2014_000000020903.jpg', 'COCO_train2014_000000019818.jpg', 'COCO_train2014_000000006842.jpg', 'COCO_train2014_000000033074.jpg', 'COCO_train2014_000000024136.jpg', 'COCO_train2014_000000032655.jpg', 'COCO_train2014_000000009195.jpg', 'COCO_train2014_000000030391.jpg', 'COCO_train2014_000000011146.jpg', 'COCO_train2014_000000022026.jpg', 'COCO_train2014_000000014774.jpg', 'COCO_train2014_000000017481.jpg', 'COCO_train2014_000000019023.jpg', 'COCO_train2014_000000007584.jpg',

Token indices sequence length is longer than the specified maximum sequence length for this model (704 > 512). Running this sequence through the model will result in indexing errors



q0 (Imagem base: 32275):
Original: The vanity contains two sinks with a towel for each.
Expandida: The vanity contains two sinks with a towel for each. A short image caption: a bathroom with a double sink and a mirror A short image caption: a bathroom with two sinks and a shower A short image caption: a bathroom with a double sink and a shower A short image caption: a bathroom with a sink, mirror, and towels A short image caption: a man taking a picture of a bathroom with a marble counter A short image caption: a bathroom with a toilet, sink, and towels A short image caption: a bathroom with a sink, mirror, toilet and a light A short image caption: a bathroom sink with a mirror and a toilet paper roll A short image caption: a bathroom with a sink, mirror, and towels A short image caption: a bathroom sink with a towel and a vase of flowers A short image caption: a bathroom with a sink, mirror and shelf A short image caption: two cats in the sinks of a bathroom A short image caption: a 

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


Streaming output truncated to the last 5000 lines.
Feedback gerado: {'q95': {'caption': 'A woman riding a bike with a basket while talking on a cell phone.', 'image_name': 3988, 'relevant_images': [3988, 16616, 8055, 27227, 17520, 26132, 5638, 8657, 34611, 27142, 28555, 16737, 8309], 'total_relevantes': 13}}
Recall@40 na iteração 1: 0.3250

q95 (Imagem base: 3988):
Original: A woman riding a bike with a basket while talking on a cell phone.
Expandida: A woman riding a bike with a basket while talking on a cell phone. A short image caption: a woman riding a bike with a basket on it A short image caption: a woman riding a bike on a city street A short image caption: a man sitting on a bike in front of a store A short image caption: a woman sitting on a bench in a park A short image caption: a couple of people walking down a path near a lake A short image caption: a woman standing on a lawn mower talking on a cell phone A short image caption: a couple of people riding a motorcycle down a 

In [ ]:
resultados_cosine_keywords = pipeline_interativo_cosine(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)



########## Processando query q0 ##########
Categoria alvo inicial: sink

=== Iteração 1 para query q0 ===

Query: The vanity contains two sinks with a towel for each.
Método: cosine
Top imagens: ['COCO_train2014_000000004830.jpg', 'COCO_train2014_000000002197.jpg', 'COCO_train2014_000000032275.jpg', 'COCO_train2014_000000012103.jpg', 'COCO_train2014_000000017644.jpg', 'COCO_train2014_000000020652.jpg', 'COCO_train2014_000000016543.jpg', 'COCO_train2014_000000002024.jpg', 'COCO_train2014_000000018820.jpg', 'COCO_train2014_000000020903.jpg', 'COCO_train2014_000000019818.jpg', 'COCO_train2014_000000006842.jpg', 'COCO_train2014_000000033074.jpg', 'COCO_train2014_000000024136.jpg', 'COCO_train2014_000000032655.jpg', 'COCO_train2014_000000009195.jpg', 'COCO_train2014_000000030391.jpg', 'COCO_train2014_000000011146.jpg', 'COCO_train2014_000000022026.jpg', 'COCO_train2014_000000014774.jpg', 'COCO_train2014_000000017481.jpg', 'COCO_train2014_000000019023.jpg', 'COCO_train2014_000000007584.jpg'

Token indices sequence length is longer than the specified maximum sequence length for this model (710 > 512). Running this sequence through the model will result in indexing errors



q0 (Imagem base: 32275):
Original: The vanity contains two sinks with a towel for each.
Expandida: The vanity contains two sinks with a towel for each. A short image caption: a bathroom with a double sink and a mirror A short image caption: a bathroom with two sinks and a shower A short image caption: a bathroom with a double sink and a shower A short image caption: a bathroom with a sink, mirror, and towels A short image caption: a man taking a picture of a bathroom with a marble counter A short image caption: a bathroom with a toilet, sink, and towels A short image caption: a bathroom with a sink, mirror, toilet and a light A short image caption: a bathroom sink with a mirror and a toilet paper roll A short image caption: a bathroom with a sink, mirror, and towels A short image caption: a bathroom sink with a towel and a vase of flowers A short image caption: a bathroom with a sink, mirror and shelf A short image caption: two cats in the sinks of a bathroom A short image caption: a 

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


Streaming output truncated to the last 5000 lines.
Feedback gerado: {'q95': {'caption': 'A woman riding a bike with a basket while talking on a cell phone.', 'image_name': 3988, 'relevant_images': [3988, 16616, 9999, 1315], 'total_relevantes': 4}}
Recall@40 na iteração 1: 0.1000

q95 (Imagem base: 3988):
Original: A woman riding a bike with a basket while talking on a cell phone.
Expandida: A woman riding a bike with a basket while talking on a cell phone. A short image caption: a woman riding a bike with a basket on it A short image caption: a woman riding a bike on a city street A short image caption: a man standing on a street corner in a city A short image caption: a woman riding a motorcycle down a street
Denoised: a woman riding a motorcycle down a street
Consulta expandida: a woman riding a motorcycle down a street

=== Iteração 2 para query q95 ===

Query: a woman riding a motorcycle down a street
Método: cosine
Top imagens: ['COCO_train2014_000000008341.jpg', 'COCO_train2014_0

In [ ]:
resultados_euclidean_keywords = pipeline_interativo_euclidean(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)

Streaming output truncated to the last 5000 lines.
Feedback gerado: {'q95': {'caption': 'A woman riding a bike with a basket while talking on a cell phone.', 'image_name': 3988, 'relevant_images': [3988, 34551, 86, 27227, 17520, 9999, 34815, 2135, 22228, 8657, 30665, 4981, 24714, 29523], 'total_relevantes': 14}}
Recall@40 na iteração 1: 0.3500

q95 (Imagem base: 3988):
Original: A woman riding a bike with a basket while talking on a cell phone.
Expandida: A woman riding a bike with a basket while talking on a cell phone. A short image caption: a woman riding a bike with a basket on it A short image caption: a woman riding a bike with an umbrella A short image caption: a man riding a motorcycle on a dirt road A short image caption: a woman sitting on a bench in a park A short image caption: a couple of people walking down a path near a lake A short image caption: a man standing on a street corner in a city A short image caption: a man and a woman with bikes standing next to a train A sh

In [ ]:
# summary
def denoise_chain_of_thought(query_expandida):
    prompt = (
        "Given the image descriptions, generate the topic of this image.\n\n"
        "Image captions:\n"
        f"{query_expandida}\n\n"
    )

    response = llm(prompt, max_new_tokens=100)[0]["generated_text"].strip()

    return response

In [ ]:
resultados_faiss_summary = pipeline_interativo_faiss(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)

In [ ]:
resultados_cosine_summary = pipeline_interativo_cosine(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)


In [ ]:
resultados_euclidean_summary = pipeline_interativo_euclidean(
    queries_reduzidas=queries_reduzidas,
    annotations=coco_data['annotations'],
    id_para_categoria=id_para_categoria,
    image_embeddings=image_embeddings,
    clip_model=clip_model,
    clip_processor=clip_processor,
    filename_to_id_dict=filename_to_id_dict
)